In [ ]:
import numpy as np
import plotly
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from fastoad.io import VariableIO

COLS = plotly.colors.DEFAULT_PLOTLY_COLORS

def drone_geometry_plot(
    aircraft_file_path: str, name=None, fig=None, file_formatter=None
) -> go.FigureWidget:
    """
    Returns a figure plot of the top view of the wing.
    Different designs can be superposed by providing an existing fig.
    Each design can be provided a name.

    :param aircraft_file_path: path of data file
    :param name: name to give to the trace added to the figure
    :param fig: existing figure to which add the plot
    :param file_formatter: the formatter that defines the format of data file. If not provided, default format will
                           be assumed.
    :return: wing plot figure
    """
    variables = VariableIO(aircraft_file_path, file_formatter).read()

    Lbra = variables['data:structure:arms:length'].value[0]
    Dpro = variables['data:propeller:diameter'].value[0]
    Narm = variables['data:structure:arms:arm_number'].value[0]
    Npro_arm = variables['data:propeller:prop_number_per_arm'].value[0]
    
    wing_kink_leading_edge_x = variables["data:geometry:wing:kink:leading_edge:x:local"].value[0]
    wing_tip_leading_edge_x = variables["data:geometry:wing:tip:leading_edge:x:local"].value[0]
    wing_root_y = variables["data:geometry:wing:root:y"].value[0]
    wing_kink_y = variables["data:geometry:wing:kink:y"].value[0]
    wing_tip_y = variables["data:geometry:wing:tip:y"].value[0]
    wing_root_chord = variables["data:geometry:wing:root:chord"].value[0]
    wing_kink_chord = variables["data:geometry:wing:kink:chord"].value[0]
    wing_tip_chord = variables["data:geometry:wing:tip:chord"].value[0]

    mean_aerodynamic_chord = variables["data:geometry:wing:MAC:length"].value[0]
    mac25_x_position = variables["data:geometry:wing:MAC:at25percent:x"].value[0]
    distance_root_mac_chords = variables["data:geometry:wing:MAC:leading_edge:x:local"].value[0]
    # pylint: disable=invalid-name # that's a common naming
    y = np.array(
        [0, wing_root_y, wing_kink_y, wing_tip_y, wing_tip_y, wing_kink_y, wing_root_y, 0, 0]
    )
    # pylint: disable=invalid-name # that's a common naming
    y = np.concatenate((-y, y))

    # pylint: disable=invalid-name # that's a common naming
    x = np.array(
        [
            0,
            0,
            wing_kink_leading_edge_x,
            wing_tip_leading_edge_x,
            wing_tip_leading_edge_x + wing_tip_chord,
            wing_kink_leading_edge_x + wing_kink_chord,
            wing_root_chord,
            wing_root_chord,
            0,
        ]
    )

    x = x + mac25_x_position - 0.25 * mean_aerodynamic_chord - distance_root_mac_chords
    # pylint: disable=invalid-name # that's a common naming
    x = np.concatenate((x, x))

    if fig is None:
        fig = go.Figure()

    scatter = go.Scatter(x=y, y=x, mode="lines+markers", name=name)

    fig.add_trace(scatter)

    fig.layout = go.Layout(yaxis=dict(scaleanchor="x", scaleratio=1))

    fig = go.FigureWidget(fig)

    fig.update_layout(
        title_text="Wing Geometry", title_x=0.5, xaxis_title="y", yaxis_title="x",
    )

    return fig

In [85]:
import numpy as np
import plotly
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from fastoad.io import VariableIO

COLS = plotly.colors.DEFAULT_PLOTLY_COLORS

Dout = 0.16
Lbra = 1
#Dpro = variables['data:propeller:diameter'].value[0]
Narm = 8 # variables['data:structure:arms:arm_number'].value[0]
#Npro_arm = variables['data:propeller:prop_number_per_arm'].value[0]

arm_angle = np.zeros(Narm)
for i in range(Narm):
    arm_angle[i] = i/Narm*360 * np.pi / 180

    
def beam_cylinder(r, h, psi, bp=0, nt=100, nv =50):
    """
    parametrize the cylinder of radius r, height h, base point bp
    """
    # Cylindrical coordinates
    theta = np.linspace(0, 2*np.pi, nt)
    axis = np.linspace(bp, bp+h, nv)
    theta, axis = np.meshgrid(theta, axis)
    
    # cylinder points
    u = axis
    v = r*np.cos(theta)
    w = r*np.sin(theta)
    
    # rotate cylinder around z=w axis
    x = u*np.cos(psi) - v*np.sin(psi)
    y = u*np.sin(psi) + v*np.cos(psi)
    z = w
    
    return x,y,z

def beam_rectangular(a,b,c, psi, bp=0):
    """
    parametrize the cube of dimension a*b*c, with base point bp
    """
    # Spherical coordinates
    phi = np.arange(1,10,2)*np.pi/4
    Phi, Theta = np.meshgrid(phi, phi)
    
    # cube points
    u = c*np.cos(Theta)/np.sqrt(2) + c/2 + bp
    v = a*np.cos(Phi)*np.sin(Theta)
    w = b*np.sin(Phi)*np.sin(Theta)
    
    # rotate around z=w axis
    x = u*np.cos(psi) - v*np.sin(psi)
    y = u*np.sin(psi) + v*np.cos(psi)
    z = w
    
    return x,y,z


def motor_cylinder(r, h, psi, bp=(0,0), nt=100, nv =50):
    """
    parametrize the cylinder of radius r, height h, base point bp(radial,z)
    """
    # Cylindrical coordinates
    theta = np.linspace(0, 2*np.pi, nt)
    axis = np.linspace(bp[1], bp[1] + h, nv)
    theta, axis = np.meshgrid(theta, axis)
    
    # cylinder points
    u = bp[0] + r*np.sin(theta)
    v = r*np.cos(theta)
    w = axis
    
    # rotate cylinder around z=w axis
    x = u*np.cos(psi) - v*np.sin(psi)
    y = u*np.sin(psi) + v*np.cos(psi)
    z = w
    
    return x,y,z

def blade(r, beta, c, angle, psi, bp=(0,0), nt=100, nv =50):
    """
    parametrize the propeller of radius r, pitch angle beta, chord c, base point bp(radial,z)
    """
    # Spherical coordinates
    phi = np.arange(1,10,2)*np.pi/4
    Phi, Theta = np.meshgrid(phi, phi)
    
    # cube points
    u1 = r*np.cos(Theta)/np.sqrt(2) + r/2
    v1 = c*np.cos(Phi)*np.sin(Theta)
    w1 = 0.01*2*r*np.sin(Phi)*np.sin(Theta)
    
    # rotate around u axis for pitch angle
    u2 = u1
    v2 = v1*np.cos(beta) - w1*np.sin(beta)
    w2 = v1*np.sin(beta) + w1*np.cos(beta)
    
    # rotate around w axis for blade position around shaft
    u = u2*np.cos(angle) - v2*np.sin(angle) + bp[0]
    v = u2*np.sin(angle) + v2*np.cos(angle)
    w = w2
    
    # rotate around z axis
    x = u*np.cos(psi) - v*np.sin(psi)
    y = u*np.sin(psi) + v*np.cos(psi)
    z = w + bp[1]
    
    return x,y,z

r_arm = Dout/2
l_arm = 0.5
a_arm = 0.05
b_arm = 0.04
h_mot = 0.06
r_mot = 0.7*h_mot
r_prop = 0.2
beta = 0.45
chord = 0.03
N_blades = 2

data = []
for i in range(Narm):
    psi = i/Narm*360 * np.pi / 180  # arm angle
    
    # FRAME
    x, y, z = beam_cylinder(r_arm, l_arm, psi, bp=r_arm)
    beam = go.Surface(x=x, y=y, z=z,
                     showscale=False,
                     opacity=1.0)
    #data.append(cyl)
    
    x, y, z = beam_rectangular(a_arm,b_arm,l_arm,psi, bp=a_arm)
    beam = go.Surface(x=x, y=y, z=z,
                     showscale=False,
                     opacity=1.0)
    data.append(beam)
    
    # MOTORS
    x, y, z = motor_cylinder(r_mot, h_mot, psi, bp=(a_arm + l_arm - r_mot, b_arm/2))
    motor = go.Surface(x=x, y=y, z=z,
                     showscale=False,
                     opacity=1.0)
    data.append(motor)
    
    # PROPELLERS
    for j in range(N_blades):
        angle = j/N_blades*360 * np.pi / 180 # blade angle position around shaft
        x, y, z = blade(r_prop, beta, chord, angle, psi, bp=(a_arm + l_arm - r_mot, b_arm/2 + h_mot))
        prop = go.Surface(x=x, y=y, z=z,
                         showscale=False,
                         opacity=1.0)
        data.append(prop)

#layout = go.Layout(scene_xaxis_visible=False, scene_yaxis_visible=False, scene_zaxis_visible=False, scene = dict(aspectmode='data'))
layout = go.Layout(scene = dict(aspectmode='data'))
fig =  go.Figure(data, layout=layout)
fig = go.FigureWidget(fig)
fig.show()